In [1]:
import vectorbtpro as vbt
from numba import njit

/Users/ericervin/opt/anaconda3/envs/datascience/lib/python3.10/site-packages/numba/core/decorators.py:262: NumbaDeprecationWarning: numba.generated_jit is deprecated. Please see the documentation at: https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-generated-jit for more information and advice on a suitable replacement.
  warnings.warn(msg, NumbaDeprecationWarning)


In [2]:
# From documentation. this clarifies quite a bit
# Enter randomly, exit randomly but only if in profit
@njit
def signal_func_nb(c, entries, exits):
    is_entry = vbt.pf_nb.select_nb(c, entries)
    is_exit = vbt.pf_nb.select_nb(c, exits)
    if is_entry:
        return True, False, False, False
    if is_exit:
        pos_info = c.last_pos_info[c.col]
        if pos_info["status"] == vbt.pf_enums.TradeStatus.Open:
            if pos_info["pnl"] >= 0:
                return False, True, False, False
    return False, False, False, False

data = vbt.YFData.fetch("BTC-USD")
entries, exits = data.run("RANDNX", n=10, unpack=True)
pf = vbt.Portfolio.from_signals(
    data,
    signal_func_nb=signal_func_nb,
    signal_args=(vbt.Rep("entries"), vbt.Rep("exits")),
    broadcast_named_args=dict(entries=entries, exits=exits),
    jitted=False  
)
pf.trades.records_readable[["Entry Index", "Exit Index", "PnL"]]

Entry Index                Exit Index          PnL
0 2015-04-10 00:00:00+00:00 2015-11-21 00:00:00+00:00    38.486137
1 2015-12-15 00:00:00+00:00 2016-10-22 00:00:00+00:00    57.133887
2 2017-02-08 00:00:00+00:00 2017-04-15 00:00:00+00:00    20.140374
3 2017-11-07 00:00:00+00:00 2019-08-13 00:00:00+00:00   113.293861
4 2019-10-20 00:00:00+00:00 2020-06-20 00:00:00+00:00    44.433617
5 2020-06-29 00:00:00+00:00 2021-03-06 00:00:00+00:00  1614.159949
6 2021-04-27 00:00:00+00:00 2023-06-06 00:00:00+00:00 -1022.964369

In [3]:
# This will also come in handy 
# Joining the ranks of stop orders, time stop orders can close out a position after a period of time or also on a specific date.
# Enter randomly, exit before the end of the month

data = vbt.YFData.fetch("BTC-USD", start="2022-01", end="2022-04")
entries = vbt.pd_acc.signals.generate_random(data.symbol_wrapper, n=10)
pf = vbt.PF.from_signals(data, entries, dt_stop="M")  # Exit before the end of the month
pf.orders.records_readable[["Fill Index", "Side", "Stop Type"]]

Fill Index  Side Stop Type
0 2022-01-09 00:00:00+00:00   Buy      None
1 2022-01-31 00:00:00+00:00  Sell        DT
2 2022-02-02 00:00:00+00:00   Buy      None
3 2022-02-28 00:00:00+00:00  Sell        DT
4 2022-03-09 00:00:00+00:00   Buy      None
5 2022-03-31 00:00:00+00:00  Sell        DT

In [4]:
# Regular metrics such as MAE and MFE represent only the final point of each trade, but what if we would like to see their development during each trade? You can now analyze expanding trade metrics as DataFrames!
# Visualize the expanding MFE using projections
data = vbt.YFData.fetch("BTC-USD")
pf = vbt.PF.from_random_signals(data, n=50, tp_stop=0.5)
pf.trades.plot_expanding_mfe_returns().show()


In [5]:
# Limit and stop orders can also be defined using a target price rather than a delta.
data = vbt.YFData.fetch("BTC-USD")
pf = vbt.PF.from_random_signals(
    data, 
    n=100, 
    sl_stop=data.low.vbt.ago(10), # This is perfect for our double peak concept
    delta_format="target"
)
sl_orders = pf.orders.stop_type_sl
signal_index = pf.wrapper.index[sl_orders.signal_idx.values]
hit_index = pf.wrapper.index[sl_orders.idx.values]
hit_after = hit_index - signal_index
hit_after

TimedeltaIndex([ '1 days',  '1 days',  '1 days',  '1 days',  '1 days',
                 '1 days',  '1 days',  '1 days',  '1 days',  '1 days',
                 '1 days',  '9 days',  '1 days',  '3 days',  '1 days',
                 '1 days',  '1 days',  '1 days',  '1 days',  '1 days',
                 '1 days',  '1 days',  '1 days',  '1 days',  '1 days',
                 '1 days', '10 days',  '1 days',  '1 days',  '1 days',
                 '1 days',  '1 days',  '1 days',  '1 days',  '1 days',
                 '1 days',  '1 days',  '1 days',  '1 days',  '1 days',
                 '1 days',  '1 days',  '9 days',  '5 days',  '1 days',
                '11 days',  '1 days',  '1 days',  '1 days',  '1 days',
                 '1 days',  '1 days',  '1 days',  '1 days',  '1 days',
                 '1 days',  '1 days',  '1 days', '16 days',  '1 days',
                 '1 days'],
               dtype='timedelta64[ns]', name='Date', freq=None)

In [72]:
from numba import njit
import pandas as pd
import numpy as np
import talib
import vectorbtpro as vbt
from vectorbtpro.portfolio.nb.core import register_jitted, tp
from vectorbtpro.utils.template import Rep, RepEval, RepFunc

vbt.settings.set_theme("dark")
vbt.settings['plotting']['layout']['width'] = 800
vbt.settings['plotting']['layout']['height'] = 300

data = vbt.YFData.fetch(['SPY'], missing_index='drop')
TALIB_RSI = vbt.IndicatorFactory.from_talib("RSI")

  0%|          | 0/1 [00:00<?, ?it/s]

symbol                            SPY
Date                                 
1993-01-29 00:00:00-05:00   25.015135
1993-02-01 00:00:00-05:00   25.140210
1993-02-02 00:00:00-05:00   25.229554
1993-02-03 00:00:00-05:00   25.372495
1993-02-04 00:00:00-05:00   25.426099
...                               ...
2023-05-31 00:00:00-04:00  416.220001
2023-06-01 00:00:00-04:00  416.790009
2023-06-02 00:00:00-04:00  423.950012
2023-06-05 00:00:00-04:00  426.369995
2023-06-06 00:00:00-04:00  425.989990

[7643 rows x 1 columns]

In [93]:


@njit
def produce_oscillator_signals(ind, entry, exit):
    signals = np.where( ind > exit, -1, 0)
    signals = np.where( (ind < entry), 1, signals)
    return signals

def custom_indicator(close, period = 14, entry_level = 30, exit_level = 70):
    rsi = TALIB_RSI.run(close, period).real.to_numpy()
    return produce_oscillator_signals(rsi, entry_level, exit_level)

ind = vbt.IndicatorFactory(
    class_name = "Oscillator",
    short_name = "osc",
    input_names = ["close"],
    param_names = ["period", "entry_level", "exit_level"],
    output_names = ["value"]
).with_apply_func(
    custom_indicator,
    period = 14,
    entry_level = 30,
    exit_level = 70,
)

my_signals = ind.run(
    data.get('Close'),
    period=2,
    entry_level=np.arange(10, 40, step=5, dtype=int),
    exit_level=np.arange(60, 90, step=5, dtype=int),
    param_product = True,
    execute_kwargs=dict(show_progress=True),
)
pf = vbt.Portfolio.from_signals(
    open=data.open,
    high=data.high,
    low=data.low,
    close=data.close,
    long_entries=my_signals.value == 1,
    long_exits=my_signals.value == -1,
    init_cash=10000,
    fees=0.0,
    fixed_fees=0.0,
    slippage=0.0,
    freq='1D',
    size_type='percent100',
    size=100,
    price="nextopen",
)

df = pf.stats([
    'total_trades',
    'profit_factor',
    'total_time_exposure',
    'win_rate',
    'avg_winning_trade',
    'avg_losing_trade',
    'avg_winning_trade_duration',
    'avg_losing_trade_duration'
], agg_func=None)


df["CAGR"] = round(100*pf.annualized_return,2)

df["CAGR/MDD"] = -1*pf.annualized_return/pf.max_drawdown

df = df[df["Total Trades"]>30]
df = df.sort_values(['Profit Factor'], ascending=[False])

display(df)

  0%|          | 0/36 [00:00<?, ?it/s]

Total Trades  Profit Factor   
osc_period osc_entry_level osc_exit_level symbol                                
2          20              85             SPY              416       2.102932  \
           25              85             SPY              463       2.079836   
           30              85             SPY              495       2.014533   
           10              85             SPY              283       1.956084   
           25              70             SPY              631       1.955804   
           20              80             SPY              473       1.950213   
                           70             SPY              548       1.931499   
           35              85             SPY              530       1.908853   
           10              70             SPY              336       1.896399   
           25              80             SPY              532       1.895018   
           15              85             SPY              363       1.886445   
           20              75             SPY              513       1.878896   
           30              70             SPY              692       1.864495   
           10              80             SPY              310       1.858275   
           25              65             SPY              670       1.844909   
           30              80             SPY              578       1.841498   
           25              75             SPY              583       1.840131   
           15              70             SPY              456       1.833167   
           10              75             SPY              322       1.822336   
           15              75             SPY              435       1.802948   
           20              65             SPY              581       1.796609   
           15              80             SPY              408       1.789159   
           30              65             SPY              749       1.786603   
           25              60             SPY              696       1.770990   
           15              65             SPY              480       1.761437   
           35              70             SPY              756       1.755240   
           20              60             SPY              601       1.752187   
           30              75             SPY              638       1.741726   
           10              60             SPY              350       1.741156   
                           65             SPY              344       1.733691   
           35              80             SPY              626       1.729393   
           30              60             SPY              785       1.727621   
           15              60             SPY              486       1.697655   
           35              65             SPY              823       1.685821   
                           75             SPY              693       1.624026   
                           60             SPY              862       1.612360   

                                                  Total Time Exposure [%]   
osc_period osc_entry_level osc_exit_level symbol                            
2          20              85             SPY                   48.410310  \
           25              85             SPY                   52.924244   
           30              85             SPY                   56.496140   
           10              85             SPY                   34.371320   
           25              70             SPY                   37.890881   
           20              80             SPY                   41.907628   
                           70             SPY                   33.625540   
           35              85             SPY                   59.256836   
           10              70             SPY                   20.829517   
           25              80             SPY                   46.434646   
           15              85             SPY  

In [96]:
best_profit_factor_params = (2,	10,	70,	'SPY')
print(pf[best_profit_factor_params].stats())
pf[best_profit_factor_params].plot().show()


Start                         1993-01-29 00:00:00-05:00
End                           2023-06-06 00:00:00-04:00
Period                               7643 days 00:00:00
Start Value                                     10000.0
Min Value                                   9907.391489
Max Value                                  80079.895994
End Value                                  80079.895994
Total Return [%]                              700.79896
Benchmark Return [%]                        1604.418797
Total Time Exposure [%]                       20.829517
Max Gross Exposure [%]                            100.0
Max Drawdown [%]                              30.596213
Max Drawdown Duration                 823 days 00:00:00
Total Orders                                        672
Total Fees Paid                                     0.0
Total Trades                                        336
Win Rate [%]                                  72.619048
Best Trade [%]                                11

In [100]:
best_tr_params = pf.total_return.idxmax()
best_tr_params

(2, 25, 70, 'SPY')

In [101]:
pf[best_tr_params].plot().show()